In [12]:
import pandas as pd
import numpy as numpy
import os
import sumolib
import copy
from tqdm import tqdm
from datetime import datetime

In [13]:
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fmins = range(midnight, next_day, 300)
m = 88 # m ranges from 26 to 287
print(fmins[m])
net = sumolib.net.readNet('../../Data/networks/SN_sample.net.xml')
inter_node = pd.read_csv('../../data/tables/inter_node.csv', index_col=0)
inter_node = inter_node[inter_node.inter_type=='parent']
histid = pd.read_csv(f'../../Data/tables/histids/histids_{fmins[m]}.csv', index_col=0)
histid = histid[histid.inter_no.isin(inter_node.inter_no.unique())]
inter2node = dict(zip(inter_node['inter_no'], inter_node['node_id']))
histid['node_id'] = histid['inter_no'].map(inter2node)
histid = histid[['node_id', 'start_unix', 'phas_A', 'phas_B', 'duration', 'inc_edge_A', 'inc_edge_B', 'out_edge_A', 'out_edge_B', 'move_A', 'move_B']]
histid = histid.reset_index(drop=True)
histid

1704406800


node_id  start_unix  phas_A  phas_B  duration       inc_edge_A  \
0        i9  1704403210       1       1        39     571510152_02   
1        i9  1704403210       2       2       101              NaN   
2        i6  1704403210       1       1        24    -571542115_01   
3        i6  1704403210       1       2        19    -571542115_01   
4        i6  1704403210       2       2        29  571500535_02.18   
..      ...         ...     ...     ...       ...              ...   
417      i8  1704406590       5       5        18     571500583_01   
418      i7  1704406630       1       1        44    -571511538_02   
419      i7  1704406630       2       2        44              NaN   
420      i7  1704406630       3       3        26    -571511538_02   
421      i7  1704406630       4       4        26              NaN   

          inc_edge_B     out_edge_A       out_edge_B  move_A  move_B  
0       571510152_01  -571510152_01  571510152_01.65       6       2  
1                NaN            NaN              NaN      17      18  
2                NaN   571500535_01              NaN       6      18  
3    571500535_02.18   571500535_01     571542115_01       6       2  
4    571500535_02.18   571511538_01     571542115_01       5       2  
..               ...            ...              ...     ...     ...  
417     571500583_01   571500617_01     571500569_01       7       4  
418     571542073_01   571542073_02     571511538_02       8       4  
419              NaN            NaN              NaN      17      18  
420     571542073_01   571542073_02     571511538_02       8       4  
421              NaN            NaN              NaN      17      18  

[422 rows x 11 columns]

In [14]:
sigtable = histid.copy()
node_ids = sorted(sigtable.node_id.unique())
nodes = [net.getNode(node_id) for node_id in node_ids]
print(node_ids)
print(nodes)

['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']
[<junction id="i0"/>, <junction id="i1"/>, <junction id="i2"/>, <junction id="i3"/>, <junction id="i6"/>, <junction id="i7"/>, <junction id="i8"/>, <junction id="i9"/>]


In [15]:
sigtable

node_id  start_unix  phas_A  phas_B  duration       inc_edge_A  \
0        i9  1704403210       1       1        39     571510152_02   
1        i9  1704403210       2       2       101              NaN   
2        i6  1704403210       1       1        24    -571542115_01   
3        i6  1704403210       1       2        19    -571542115_01   
4        i6  1704403210       2       2        29  571500535_02.18   
..      ...         ...     ...     ...       ...              ...   
417      i8  1704406590       5       5        18     571500583_01   
418      i7  1704406630       1       1        44    -571511538_02   
419      i7  1704406630       2       2        44              NaN   
420      i7  1704406630       3       3        26    -571511538_02   
421      i7  1704406630       4       4        26              NaN   

          inc_edge_B     out_edge_A       out_edge_B  move_A  move_B  
0       571510152_01  -571510152_01  571510152_01.65       6       2  
1                NaN            NaN              NaN      17      18  
2                NaN   571500535_01              NaN       6      18  
3    571500535_02.18   571500535_01     571542115_01       6       2  
4    571500535_02.18   571511538_01     571542115_01       5       2  
..               ...            ...              ...     ...     ...  
417     571500583_01   571500617_01     571500569_01       7       4  
418     571542073_01   571542073_02     571511538_02       8       4  
419              NaN            NaN              NaN      17      18  
420     571542073_01   571542073_02     571511538_02       8       4  
421              NaN            NaN              NaN      17      18  

[422 rows x 11 columns]

In [16]:
node2init = {}
for node in nodes:
    node_id = node.getID()
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        for j, cj in conns:
            if ci.getTo() == cj.getTo():
                continue
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    node2init[node_id] = state

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in sigtable.iterrows():
    node_id = row['node_id']
    inc_edge_A = row.inc_edge_A
    inc_edge_B = row.inc_edge_B
    out_edge_A = row.out_edge_A
    out_edge_B = row.out_edge_B
    move_A = row['move_A']
    move_B = row['move_B']

    if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
        continue
    else:
        inc_edge_A = net.getEdge(inc_edge_A)
        out_edge_A = net.getEdge(out_edge_A)
        for conn in inc_edge_A.getConnections(out_edge_A):
            index = conn.getTLLinkIndex()
            if index >= 0:
                node2init[node_id][index] = 'r'

    if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
        continue
    else:
        inc_edge_B = net.getEdge(inc_edge_B)
        out_edge_B = net.getEdge(out_edge_B)
        for conn in inc_edge_B.getConnections(out_edge_B):
            index = conn.getTLLinkIndex()
            if index >= 0:
                node2init[node_id][index] = 'r'
for node_id in node_ids:
    print(node_id, "".join(node2init[node_id]))

i0 grrrgrrrgrrrrrgrr
i1 grrrrrrgrr
i2 rrggrrr
i3 grrrrgrrrrgrrrrgrrrr
i6 grrrgrrrrgrrgrrr
i7 rrrggrr
i8 grrrrrrrgrrrgrrr
i9 rrrr


In [17]:
print(node2init['i6'])
state = copy.deepcopy(node2init)['i6']
state[0] = 'G'
print(state)
print(node2init['i6'])

['g', 'r', 'r', 'r', 'g', 'r', 'r', 'r', 'r', 'g', 'r', 'r', 'g', 'r', 'r', 'r']
['G', 'r', 'r', 'r', 'g', 'r', 'r', 'r', 'r', 'g', 'r', 'r', 'g', 'r', 'r', 'r']
['g', 'r', 'r', 'r', 'g', 'r', 'r', 'r', 'r', 'g', 'r', 'r', 'g', 'r', 'r', 'r']


In [28]:
sigtable = histid.copy()
sigtable['init_state'] = sigtable['node_id'].map(node2init)
for i, row in sigtable.iterrows():
    node_id = row.node_id
    inc_edge_A = row.inc_edge_A
    inc_edge_B = row.inc_edge_B
    out_edge_A = row.out_edge_A
    out_edge_B = row.out_edge_B
    state = copy.deepcopy(node2init)[node_id]

    if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
        continue
    else:
        inc_edge_A = net.getEdge(inc_edge_A)
        out_edge_A = net.getEdge(out_edge_A)
        for conn in inc_edge_A.getConnections(out_edge_A):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        sigtable.at[i, 'state'] = ''.join(state)

    if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
        continue
    else:
        inc_edge_B = net.getEdge(inc_edge_B)
        out_edge_B = net.getEdge(out_edge_B)
        for conn in inc_edge_B.getConnections(out_edge_B):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        sigtable.at[i, 'state'] = ''.join(state)
sigtable = sigtable.dropna(subset='state')
sigtable = sigtable.reset_index(drop=True)
sigtable['phase_sumo'] = sigtable.groupby(['node_id', 'start_unix']).cumcount()
sigtable = sigtable[['node_id', 'start_unix', 'phase_sumo', 'duration', 'state']]
sigtable = sigtable.sort_values(by=['start_unix', 'node_id'])
print(datetime.fromtimestamp(fmins[m]))
display(sigtable[:30])

2024-01-05 07:20:00


node_id  start_unix  phase_sumo  duration                 state
1       i6  1704403210           0        24      grrrgGGGrgrrgrrr
2       i6  1704403210           1        19      grrrgGGGrgrrgGGr
3       i6  1704403210           2        29      grrrgrrrrgrrgGGG
4       i6  1704403210           3        56      gGGGgrrrrgrrgrrr
5       i6  1704403210           4        22      grrrgrrrrgGGgrrr
0       i9  1704403210           0        39                  GGGG
6       i3  1704403220           0        38  gGGGrgrrrrgGGGrgrrrr
7       i3  1704403220           1        39  grrrGgrrrrgrrrGgrrrr
8       i3  1704403220           2        40  grrrrgrrrrgrrrrgGGGG
9       i3  1704403220           3        23  grrrrgGGGGgrrrrgrrrr
10      i2  1704403230           0        36               GGggGGG
11      i2  1704403230           1        20               rrggrrr
12      i2  1704403230           2        26               rrggGGG
13      i1  1704403250           0        37            gGGGGGrgrr
14      i1  1704403250           1        73            grrGGGGgrr
15      i1  1704403250           2        40            grrrrrrgGG
16      i0  1704403270           0        37     gGGrgrrrgGGGGrgrr
17      i0  1704403270           1        39     grrGgrrrgrrrrGgrr
18      i0  1704403270           2        25     grrrgGGGgrrrrrgrr
19      i0  1704403270           3        30     grrrgGGrgrrrrrgGr
20      i0  1704403270           4        29     grrrgrrrgrrrrrgGG
21      i7  1704403320           0        33               GGrggGG
22      i7  1704403320           1        26               GGrggGG
23      i9  1704403350           0        39                  GGGG
24      i3  1704403360           0        38  gGGGrgrrrrgGGGrgrrrr
25      i3  1704403360           1        39  grrrGgrrrrgrrrGgrrrr
26      i3  1704403360           2        40  grrrrgrrrrgrrrrgGGGG
27      i3  1704403360           3        23  grrrrgGGGGgrrrrgrrrr
28      i6  1704403360           0        24      grrrgGGGrgrrgrrr
29      i6  1704403360           1        19      grrrgGGGrgrrgGGr

In [8]:
strings = ['<tlLogics>\n']
for key, group in sigtable.groupby(['start_unix', 'node_id']):
    start_unix = key[0]
    node_id = key[1]
    strings.append(f'    <tlLogic id="{node_id}" type="traffic_light" programID="{key}" offset="{start_unix}">\n')
    for i, row in group.iterrows():
        duration = row.duration
        state = row.state
        strings.append(f'      <phase duration="{duration}" state="{state}"/>\n')
    strings.append('    </tlLogic>\n')
strings.append('</tlLogics>')
strings = ''.join(strings)
# 저장
path_output = '../../Data/networks/SN_sample.tll.xml'
with open(path_output, 'w') as f:
    f.write(strings)
print(strings)

<tlLogics>
    <tlLogic id="i6" type="traffic_light" programID="(1704403210, 'i6')" offset="1704403210">
      <phase duration="24" state="grrrgGGGrgrrgrrr"/>
      <phase duration="19" state="grrrgGGGrgrrgGGr"/>
      <phase duration="29" state="grrrgrrrrgrrgGGG"/>
      <phase duration="56" state="gGGGgrrrrgrrgrrr"/>
      <phase duration="22" state="grrrgrrrrgGGgrrr"/>
    </tlLogic>
    <tlLogic id="i9" type="traffic_light" programID="(1704403210, 'i9')" offset="1704403210">
      <phase duration="39" state="GGGG"/>
    </tlLogic>
    <tlLogic id="i3" type="traffic_light" programID="(1704403220, 'i3')" offset="1704403220">
      <phase duration="38" state="gGGGrgrrrrgGGGrgrrrr"/>
      <phase duration="39" state="grrrGgrrrrgrrrGgrrrr"/>
      <phase duration="40" state="grrrrgrrrrgrrrrgGGGG"/>
      <phase duration="23" state="grrrrgGGGGgrrrrgrrrr"/>
    </tlLogic>
    <tlLogic id="i2" type="traffic_light" programID="(1704403230, 'i2')" offset="1704403230">
      <phase duration="3

In [9]:
import pandas as pd
path = 'one_cycle.csv'
df = pd.read_csv(path)

# 적당히 지정하세요
node_id = df['node_id'][0]
offset = 999

# xml양식대로 작성
strings = ['<tlLogics>\n']
strings.append(f'    <tlLogic id="{node_id}" type="static" programID="{node_id}" offset="{offset}">\n')
for i, row in df.iterrows():
    dur = row['dura']
    state = row['signal']
    strings.append(f'      <phase duration="{dur}" state="{state}"/>\n')
strings.append('    </tlLogic>\n')
strings.append('</tlLogics>')
strings = ''.join(strings)
print(strings)

# 저장
path_output = 'example.tll.xml'
with open(path_output, 'w') as f:
    f.write(strings)

FileNotFoundError: [Errno 2] No such file or directory: 'one_cycle.csv'